# Similarity-based Competency Extraction Service

* First we check if the required packages are installed. 

spaCy: an open-source software library for advanced natural language processing, written in the programming languages Python and Cython  

NumPy: a library for the Python programming language, adding support for large, multi-dimensional arrays and matrices, along with a large collection of high-level mathematical functions to operate on these arrays

TensorFlow: a free and open-source software library for machine learning and artificial intelligence.

pandas: a software library written for the Python programming language for data manipulation and analysis

In [83]:
# !pip3 install -U pip setuptools wheel
# !pip3 install -U spacy
# !python3 -m spacy download de_core_news_lg
# !pip3 install numpy
# !pip3 install absl-py
# !pip3 install --upgrade tensorflow
# !pip3 install "tensorflow>=2.0.0"
# !pip3 install --upgrade tensorflow-hub
# !pip3 install tensorflow_text
# !pip3 install --ignore-installed Pillow==9.0.0
# !pip3 install pandas
# !pip3 install xmltodict

* Now we can import these packages.

In [6]:
#@title Load the Universal Sentence Encoder's TF Hub module
from absl import logging

import tensorflow as tf
import tensorflow_text
import tensorflow_hub as hub
import numpy as np
import os
import pandas as pd
import re  # RegEx
# import seaborn as sns


import spacy
nlp = spacy.load('de_core_news_lg')

import xmltodict
import time

* We load the tensorflow module for text embedding.  

The main idea of the similarity calculation part is to vectorize the text and then calculate the cosine distance between them.
Machine learning models take vectors as input and the word embeddings give us a way to use an efficient, dense representation in which similar words have a similar encoding.  
For this, we use a pre-trained transformer model on TensorFlow hub.
This specific module is optimized for multi-word length text, such as sentences, phrases, or short paragraphs.
And it converts variable-length text into a 512 dimensional vector.

In [7]:
%%time
module_url = "https://tfhub.dev/google/universal-sentence-encoder-multilingual-large/3" 
model = hub.load(module_url)
print ("module %s loaded" % module_url)
def embed(input):
  return model(input)

2022-08-05 23:33:36.867569: I tensorflow/core/platform/cpu_feature_guard.cc:193] This TensorFlow binary is optimized with oneAPI Deep Neural Network Library (oneDNN) to use the following CPU instructions in performance-critical operations:  AVX2 FMA
To enable them in other operations, rebuild TensorFlow with the appropriate compiler flags.


module https://tfhub.dev/google/universal-sentence-encoder-multilingual-large/3 loaded
CPU times: user 4.68 s, sys: 455 ms, total: 5.14 s
Wall time: 5.51 s


## Data Preprocessing

We use the ESCO skills dataset as our corpus. You can download the latest version of it here https://esco.ec.europa.eu/en/use-esco/download

* import competency data from csv file

In [8]:
%%time
skills = pd.read_csv('../data/skills_de.csv',usecols=['conceptUri','preferredLabel'])

CPU times: user 53.7 ms, sys: 18.2 ms, total: 71.8 ms
Wall time: 84.8 ms


Note that for efficiency reasons we only use preferred term (contents of column "preferredLabel") for our extraction service.

In [9]:
skills.head(10)

conceptUri  \
0  http://data.europa.eu/esco/skill/0005c151-5b5a...   
1  http://data.europa.eu/esco/skill/00064735-8fad...   
2  http://data.europa.eu/esco/skill/000709ed-2be5...   
3  http://data.europa.eu/esco/skill/0007bdc2-dd15...   
4  http://data.europa.eu/esco/skill/00090cc1-1f27...   
5  http://data.europa.eu/esco/skill/000bb1e4-89f0...   
6  http://data.europa.eu/esco/skill/000c94d2-2a2e...   
7  http://data.europa.eu/esco/skill/000f1d3d-220f...   
8  http://data.europa.eu/esco/skill/001115fb-569f...   
9  http://data.europa.eu/esco/skill/001d46db-035e...   

                                      preferredLabel  
0                            Musikpersonal verwalten  
1              Strafvollzugsverfahren beaufsichtigen  
2            nicht unterdrückende Praktiken anwenden  
3  Einhaltung von Vorschriften von Eisenbahnfahrz...  
4                       verfügbare Dienste ermitteln  
5                 toxikologische Studien durchführen  
6         Einheitlichkeit von Kokillen gewährleisten  
7                                            Haskell  
8                                  Initiative zeigen  
9  Personal mit Blick auf die Verringerung von Le...

In [10]:
labels = skills['preferredLabel'].copy(deep=True)
labels

0                                  Musikpersonal verwalten
1                    Strafvollzugsverfahren beaufsichtigen
2                  nicht unterdrückende Praktiken anwenden
3        Einhaltung von Vorschriften von Eisenbahnfahrz...
4                             verfügbare Dienste ermitteln
                               ...                        
13886    berufliche Leistungsfähigkeit von Nutzern/Nutz...
13887             Beleuchtung in Transportgeräten einbauen
13888                     Verarbeitung natürlicher Sprache
13889                             Bauarbeiten koordinieren
13890         Absturzsicherungen und Bordbretter anbringen
Name: preferredLabel, Length: 13891, dtype: object

We use spaCy processing pipeline to do the lemmatization of each token. After lemmatization, all punctuations will  be converted to "--" and then deleted.

Since the data were obtained from the official documents of the European Commission, we did not perform data cleaning on them.

In [11]:
def labels_processing(text):
    processed = []
    for item in text:
        item = nlp(item)
        itemString = ''
        for word in item:
            word = word.lemma_.lower() # lemma_: Extract the lemma for each token
            if word != '--' and word != '' and word != ' ':
#                 if word == '\xa0': continue                    
                itemString += word + ' '
        processed.append(itemString[:-1])
    return processed

In [12]:
%%time
processedLabels = labels_processing(labels)

CPU times: user 1min 9s, sys: 552 ms, total: 1min 9s
Wall time: 1min 10s


* import descriptions data from xml file

Here you can try this descriptions_cropped.xml file to play with it. 

In [13]:
# %%time
# test = open('../data/descriptions_cropped.xml','r', encoding='ISO-8859-15').read() # read data
# test_dict = xmltodict.parse(test) # parse xml
# xmlDict = test_dict

Load all course description data from xml file

In [14]:
%%time
xml_data = open('../data/FOKUS_AWT_CompetencyExtraction_WB_Brandenburg.xml','r', encoding='ISO-8859-15').read() # read data
xmlDict = xmltodict.parse(xml_data) # parse xml

CPU times: user 6.02 s, sys: 215 ms, total: 6.23 s
Wall time: 6.24 s


In [15]:
%%time
xmlcourses = xmlDict['DEFTISCAT']['COURSETRANSACTIONS']['INSERTCOURSES']['COURSE']

CPU times: user 3 µs, sys: 0 ns, total: 3 µs
Wall time: 6.91 µs


Competency is often included in course titles. So we combine course_name and course_description.

In [16]:
%%time
coursesDict = []
for course in xmlcourses:
    coursesDict.append({"course_id": course['CS_ID'], 
                        "course_name": course['CS_NAME'],
                 "course_description": course['CS_DESC_LONG']})
courses_table = pd.DataFrame(coursesDict)
courses_table.replace([None],value='',inplace=True)
courses = courses_table['course_name'] + ' ' + courses_table['course_description']

CPU times: user 56.5 ms, sys: 26.9 ms, total: 83.4 ms
Wall time: 84.5 ms


In [17]:
courses_table

course_id  \
0      4A873264-7ADD-DE47-3039-1FDA692E8164   
1      99BEDCEB-4FF3-3F8F-88B7-B30E50638F01   
2      97FD41FD-1A91-179C-3EA5-6A23E2F436D5   
3      A0CC573A-79D7-79A4-5B22-F675C4F06950   
4      7C449EF7-12A8-82FC-0E5E-BD2885FDB93C   
...                                     ...   
16847  A1E046BE-1C4B-B977-C9B9-88D8D2860107   
16848  A1DF8EEB-D317-70BA-508F-AFC732369860   
16849  A1DD9D98-2BA3-3A11-0A24-72FC4C79422A   
16850  A1DD60F7-9B6E-ECEE-F1DF-53FED2DCCC5C   
16851  A1E01A90-D165-5959-2102-771B5459852B   

                                             course_name  \
0      "Schwierige" Klienten? - Mit Patienten, Angehö...   
1                            Aktuelles Arbeitsrecht 2022   
2      Ambulante Pflege - Rechtssicher Handeln und Ha...   
3      Aufgaben des gesetzlichen Betreuers - Zur Refo...   
4      Basisqualifikation für ungelernte Pflegekräfte...   
...                                                  ...   
16847  5 Monate Weiterbildung: Organisation & Führung...   
16848                   Conversion und Usability Experte   
16849                  Digital Transformation Management   
16850                        E-Commerce Geschäftsmodelle   
16851                Experte im Digital Content Creation   

                                      course_description  
0      - Analyse strapaziöser Gesprächsmuster\n- Schw...  
1      Kurzbeschreibung\nDas Arbeitsrecht unterliegt ...  
2      - Grundlagen der straf- und zivilrechtlichen H...  
3      Kurzbeschreibung\nNoch im Jahr 2020 plant der ...  
4      - Alten- und Krankenpflege\n  . Körperpflege\n...  
...                                                  ...  
16847  Die aktuell vorherrschende Situation auf dem A...  
16848  Ziel der Maßnahme ist es den Teilnehmern eine ...  
16849  Ziel der Maßnahme ist es den Teilnehmern eine ...  
16850  Ziel der Maßnahme ist es den Teilnehmern eine ...  
16851  Die Teilnehmer werden zu einem Digital Content...  

[16852 rows x 3 columns]

In [18]:
courses

0        "Schwierige" Klienten? - Mit Patienten, Angehö...
1        Aktuelles Arbeitsrecht 2022 Kurzbeschreibung\n...
2        Ambulante Pflege - Rechtssicher Handeln und Ha...
3        Aufgaben des gesetzlichen Betreuers - Zur Refo...
4        Basisqualifikation für ungelernte Pflegekräfte...
                               ...                        
16847    5 Monate Weiterbildung: Organisation & Führung...
16848    Conversion und Usability Experte Ziel der Maßn...
16849    Digital Transformation Management Ziel der Maß...
16850    E-Commerce Geschäftsmodelle Ziel der Maßnahme ...
16851    Experte im Digital Content Creation Die Teilne...
Length: 16852, dtype: object

We found some parts of the text that were not encoded correctly. Let's correct them now.

In [19]:
%%time
length = len(courses)
for i in range(length):
    courses[i] = courses[i].replace('&#8211;','-')
    courses[i] = courses[i].replace('&#8222;','„')
    courses[i] = courses[i].replace('&#8220;','“')
    courses[i] = courses[i].replace('&#8230;','...')

CPU times: user 438 ms, sys: 4.08 ms, total: 442 ms
Wall time: 443 ms


Now we split each description in sentences.
We put the data into the spacy pipeline, remove the special symbols.  

In [20]:
%%time
def To_sentences(courses):
    courses_sent = []
    courses_sent_lemma = []
    for course in (courses):
        with nlp.select_pipes(disable=['attribute_ruler', 'ner']):
            doc = nlp(str(course))
            sentences = []
            for sent in doc.sents:
                course_processed = ''
                sents = []
                for word in sent:
                    word = word.text
                    word = word.replace('\n', ' ')
                    word = word.strip().strip('"@#$%^&*§')
                    if word == '-':
                        if course_processed != '':
                            sents.append(course_processed[:-1])
                            course_processed = ''
                        continue
                    if word.startswith('- ') and len(word) > 1:
                        word = word.replace('- ', '')
                        if course_processed != '':
                            sents.append(course_processed[:-1])
                            course_processed = ''
                    if (not re.match('\s+', word,re.I)) and word != '--' and word != '':
                        if "/-" in word: 
                            word = word.split("/-")[0]
                        if re.match(r'\,|\.|\?|\!|\)', word):
                            course_processed = course_processed[:-1] + word + ' '
                        elif re.match(r'\(',word):
                            course_processed += word
                        else:
                            course_processed += word + ' '
                sentences += sents
                if course_processed != '':
                    sentences.append(course_processed[:-1])
            courses_sent_lemma.append(sentences)
    return courses_sent_lemma

CPU times: user 4 µs, sys: 1e+03 ns, total: 5 µs
Wall time: 8.34 µs


You can try and see the processing result for the first course:

In [21]:
course_in_sentences_test = To_sentences(courses.iloc[:1])
print(courses.iloc[0])
print(course_in_sentences_test)

"Schwierige" Klienten? - Mit Patienten, Angehörigen und Kollegen clever kommunizieren - Analyse strapaziöser Gesprächsmuster
- Schwierige Klienten oder schwierige Situation?
- Was heißt es schwierige Gespräche souverän zu meistern?
- Übungen mit Videofeedback werden durchgeführt!
[['Schwierige Klienten?', 'Mit Patienten, Angehörigen und Kollegen clever kommunizieren', 'Analyse strapaziöser Gesprächsmuster', 'Schwierige Klienten oder schwierige Situation?', 'Was heißt es schwierige Gespräche souverän zu meistern?', 'Übungen mit Videofeedback werden durchgeführt!']]


To increase the precision of TF working result, course description is split into bunch of chunks with key words of competencies.
For more information see https://spacy.io/api/pipeline-functions#merge_noun_chunks

First we add 'merge_noun_chunks' to the spacy processing pipeline so that noun chunks will then be seen as a single token.

In [22]:
nlp.add_pipe('merge_noun_chunks')

<function spacy.pipeline.functions.merge_noun_chunks(doc: spacy.tokens.doc.Doc) -> spacy.tokens.doc.Doc>

In [23]:
print(nlp.pipe_names)

['tok2vec', 'tagger', 'morphologizer', 'parser', 'lemmatizer', 'attribute_ruler', 'ner', 'merge_noun_chunks']


Then we extract the Noun Phrase Chunks from the sentence.  
Chunking identifies groups of words that go together to form symbolic meaning.  
It builds upon the process Part of Speech (POS) Tagging, which is a way to describe the grammatical function of a word.


Chunking is a critical step in our approach. Because it allows us to split the course description into a collection of phrases to compare with the competencies.
Finally, we remove the stop words, punctuation and other special symbols such as dash and slash. Then we lemmatize the remaining words.


In [24]:
%%time
def Segment_processing(part_of_the_courses):
    
    # to sentences
    course_in_sentences = To_sentences(part_of_the_courses)
    
    # to chunks
    courses_chunks = []
    for course in course_in_sentences:
        course_chunks = []
        for sent in course:
            sent_chunks = []
            doc = nlp(sent)
            for tok in doc:
                with nlp.select_pipes(disable=['merge_noun_chunks','attribute_ruler', 'ner']):
                    if not re.match('\(|\)|\,|\.|\!|\?|\/',tok.text) and not tok.is_stop: 
                        tok = nlp(tok.text)
                        words = ''
                        for word in tok:
                            if not word.is_stop and word.lemma_ != '--':
                                words = words + word.lemma_ + ' '  
                        sent_chunks.append(words[:-1])
            course_chunks += sent_chunks
        courses_chunks.append(course_chunks)
    return courses_chunks


CPU times: user 3 µs, sys: 1 µs, total: 4 µs
Wall time: 5.96 µs


For example the processing result of the first course is as follow: 

In [25]:
%%time
courses_chunks_test = Segment_processing(courses.iloc[:1])
print(course_in_sentences_test)
print(courses_chunks_test)

[['Schwierige Klienten?', 'Mit Patienten, Angehörigen und Kollegen clever kommunizieren', 'Analyse strapaziöser Gesprächsmuster', 'Schwierige Klienten oder schwierige Situation?', 'Was heißt es schwierige Gespräche souverän zu meistern?', 'Übungen mit Videofeedback werden durchgeführt!']]
[['schwierige Klient', 'Patient', 'angehörige', 'Kollege', 'clever', 'kommunizieren', 'Analyse', 'strapaziös Gesprächsmuster', 'schwierig Klient', 'schwierig Situation', 'schwierig Gespräch', 'souverän', 'Meister', 'Übung', 'videofeedback', 'durchführen']]
CPU times: user 469 ms, sys: 412 ms, total: 880 ms
Wall time: 940 ms


## Embedding-phase

After the text has been processed, we now embed them as vectors.  
For efficiency, we will handle course descriptions in batches. (cf. function Save_results)

In [26]:
def Course_Embedding(courses_chunks):
    courses_chunks_embed = []
    for course in courses_chunks:
        courses_chunks_embed.append(embed(course))
    return courses_chunks_embed

In [27]:
%%time
labels_embed = embed(processedLabels)

CPU times: user 2min, sys: 36.6 s, total: 2min 37s
Wall time: 34 s


## Similarity

We calculate the cosine distance for the transformed text of competency and word chunks of course descriptions. 

In [28]:
%%time
def Similarity(labels, courses):
    result = []
    for course in courses:
        result.append(np.dot(labels, np.transpose(course)))
    return result

CPU times: user 3 µs, sys: 1e+03 ns, total: 4 µs
Wall time: 8.34 µs


In [29]:
%%time
def Get_relations(relations,skills,courses_table,course_idx,benchmark,courses_chunks):

    idx = 0
    counter = 0

    df_relations = pd.DataFrame(columns = ['conceptUri'])
    for relationship in relations:
        print('course: ', course_idx)
        competency_idx = np.where(relationship>benchmark) 

        print('numbers of extracted competency: ', len(competency_idx[0]))
        for j in range(len(competency_idx[0])):
            print(processedLabels[competency_idx[0][j]],'--', courses_chunks[idx][competency_idx[1][j]])
            
        competency = set(skills.loc[list(competency_idx[0]),'conceptUri'])
        competency_uri = pd.DataFrame(competency,columns=['conceptUri'], index=[courses_table.iloc[course_idx]['course_id']]*len(competency)) 

        print(' ------')
#         print(courses[course_idx])
        print('\n')

        df_relations = pd.concat([df_relations,competency_uri])
    
        course_idx += 1 
        
#         test:
        idx += 1
        counter += len(competency)
    print('number of extracted competency', counter)
    print('\n', df_relations)

    return df_relations

CPU times: user 3 µs, sys: 1e+03 ns, total: 4 µs
Wall time: 6.91 µs


The performance of this method is strongly related to the setting of the threshold value.
Theoretically, after Setting different thresholds to determine whether the texts are similar, comparing the results, and finding the threshold that makes the highest F-score.
We can use this f-score to evaluate our method.
However, as we said in the section on the evaluation method,
We do not have a reliable test dataset and thus no f-score.
We have tried several thresholds and made a manual selection based on the output results.

In [30]:
def Competence_extraction(courses,course_start_idx,labels,benchmark):
    courses_chunks = Segment_processing(courses)
    courses_embed = Course_Embedding(courses_chunks)
    calculated_results = Similarity(labels, courses_embed)
    return Get_relations(calculated_results,skills,courses_table,course_start_idx,benchmark,courses_chunks)

In [31]:
%%time
def Save_results(courses,benchmark):
    for i in range(27):
        if i < 23:
            continue
        start = i * 600
        end = (i+1) * 600
        courses_div = courses.iloc[start:end]
        relations = Competence_extraction(courses_div,start,labels_embed,benchmark)
        relations.to_csv(path_or_buf="./relations_part_"+str(i+1)+".csv" ,columns=['conceptUri'], index_label='course_id')
    Competence_extraction(courses.iloc[27*600:],27*600,labels_embed,benchmark).to_csv(path_or_buf="./relations_part_28.csv" ,columns=['conceptUri'], index_label='course_id')


CPU times: user 6 µs, sys: 1e+03 ns, total: 7 µs
Wall time: 9.06 µs


In [ ]:
Save_results(courses,benchmark=0.85)

course:  0
numbers of extracted competency:  2
kommunikation -- kommunizieren
schwierig situation bewältigen -- schwierig Situation
 ------


course:  1
numbers of extracted competency:  1
arbeitsrecht -- Arbeitsrecht
 ------


course:  2
numbers of extracted competency:  3
ambulant pflege anbieten -- ambulant Pflege
dokumentationsart -- Dokumentation
risikomanagement -- Risikomanagement
 ------


course:  3
numbers of extracted competency:  1
planen -- planen
 ------


course:  4
numbers of extracted competency:  3
ernährung -- Ernährung
qualität gewährleisten -- Qualitätssicherung
qualitätssicherung durchführen -- Qualitätssicherung
 ------


course:  5
numbers of extracted competency:  1
verpflichtung erfüllen -- verpflichtend
 ------


course:  6
numbers of extracted competency:  1
verpflichtung erfüllen -- verpflichtend
 ------


course:  7
numbers of extracted competency:  4
verpflichtung erfüllen -- verpflichtend
kommunikation -- kommunizieren
kerze bewerten -- bewerten
kerze be

numbers of extracted competency:  13
agil projektmanagement -- agile Projektmanagement
agil projektmanagement -- agil Projektmanagement
gutachten vorbereiten -- vorbereiten
vorbereitend unterrichten -- vorbereiten
abbauvorschlag vorbereiten -- vorbereiten
arbeit leiten -- arbeiten
mikrofon benutzen -- Mikrofon
aktienmarkt -- Markt
ios -- iOS
grab vorbereiten -- vorbereiten
planen -- planen
planen -- planen
produktgestaltung entwickeln -- Produktentwicklung
 ------


course:  75
numbers of extracted competency:  7
gutachten vorbereiten -- vorbereiten
vorbereitend unterrichten -- vorbereiten
abbauvorschlag vorbereiten -- vorbereiten
grab vorbereiten -- vorbereiten
planen -- planen
planen -- planen
dach überprüfen -- prüfen
 ------


course:  76
numbers of extracted competency:  7
gutachten vorbereiten -- vorbereiten
vorbereitend unterrichten -- vorbereiten
abbauvorschlag vorbereiten -- vorbereiten
grab vorbereiten -- vorbereiten
planen -- planen
planen -- planen
dach überprüfen -- prüfen

numbers of extracted competency:  0
 ------


course:  112
numbers of extracted competency:  6
kriminologie -- Kriminologie
psychologie unterrichten -- Psychologie
psychosoziologie -- Psychologie
psychophysiologie -- Psychologie
psychologie -- Psychologie
psychopathologie -- Psychologie
 ------


course:  113
numbers of extracted competency:  4
wache stehen -- stehen
erhebungstechnik -- Technik
artikulationstechnik -- Technik
flechttechnik -- Technik
 ------


course:  114
numbers of extracted competency:  4
wache stehen -- stehen
erhebungstechnik -- Technik
artikulationstechnik -- Technik
flechttechnik -- Technik
 ------


course:  115
numbers of extracted competency:  6
arbeitsmarktangebot -- Arbeitsmarkt
arbeitsmarktangebot -- Arbeitsmarkt
r -- Z
qualitätsstandard -- geltend Qualitätsstandard
arbeitsmarkt -- Arbeitsmarkt
arbeitsmarkt -- Arbeitsmarkt
 ------


course:  116
numbers of extracted competency:  1
kreislaufwirtschaft -- Kreislaufwirtschaft
 ------


course:  117
numbers of

numbers of extracted competency:  2
vertragsvorgabe einhalten -- vertraglich Vereinbarung
konzentrieren bleiben -- konzentrieren
 ------


course:  151
numbers of extracted competency:  2
konflikt lösen -- Konflikt
kommunikationsgrundsatz -- Kommunikationsgrundlag
 ------


course:  152
numbers of extracted competency:  5
vorbereitend unterrichten -- Vorbereitung
staf -- Mitarbeiter
qualitätsmanagementsystem umsetzen -- Qualitätsmanagementsystem
wettrecht -- Gesetz
qualitätssicherungssystem -- Qualitätssicherungssystem
 ------


course:  153
numbers of extracted competency:  4
staf -- Mitarbeiter
staf -- Mitarbeiter
aktienmarkt -- Markt
gesellschaft leisten -- Gesellschaft
 ------


course:  154
numbers of extracted competency:  3
staf -- Mitarbeiter
unternehmenskultur formen -- bestehend Unternehmenskultur
entscheidung treffen -- Entscheidung
 ------


course:  155
numbers of extracted competency:  3
staf -- Mitarbeiter
unternehmenskultur formen -- bestehend Unternehmenskultur
entsche

numbers of extracted competency:  8
wache stehen -- stehen
arbeit leiten -- arbeiten
strom -- Strom
marke -- merken
papierart -- Papier
sich kreativ ausdrücken -- kreativ
kreativ denken -- kreativ
kreativ prozeß anregen -- kreativ
 ------


course:  188
numbers of extracted competency:  8
wache stehen -- stehen
arbeit leiten -- arbeiten
strom -- Strom
marke -- merken
papierart -- Papier
sich kreativ ausdrücken -- kreativ
kreativ denken -- kreativ
kreativ prozeß anregen -- kreativ
 ------


course:  189
numbers of extracted competency:  3
wache stehen -- stehen
statistik -- statistisch Wert
internet der ding -- Internet
 ------


course:  190
numbers of extracted competency:  5
wache stehen -- stehen
öffentlich gesundheitswesen -- Public-Health
konfliktmanagement -- Konfliktmanagement
projekt managen -- Projektmanagement
zeitplan verwalten -- Zeitmanagement
 ------


course:  191
numbers of extracted competency:  5
wache stehen -- stehen
öffentlich gesundheitswesen -- Public-Health
konf

...

numbers of extracted competency:  3
agil projektmanagement -- agile Projektmanagement
agil projektmanagement -- agile Projektmanagement
entscheidung treffen -- Entscheidungsfindung
 ------


course:  14134
numbers of extracted competency:  3
agil projektmanagement -- agile Projektmanagement
agil projektmanagement -- agile Projektmanagement
entscheidung treffen -- Entscheidungsfindung
 ------


course:  14135
numbers of extracted competency:  3
agil projektmanagement -- agile Projektmanagement
agil projektmanagement -- agile Projektmanagement
entscheidung treffen -- Entscheidungsfindung
 ------


course:  14136
numbers of extracted competency:  3
agil projektmanagement -- agile Projektmanagement
agil projektmanagement -- agile Projektmanagement
agil projektmanagement -- agil Projektmanagement
 ------


course:  14137
numbers of extracted competency:  3
agil projektmanagement -- agile Projektmanagement
agil projektmanagement -- agile Projektmanagement
agil projektmanagement -- agil Proje

numbers of extracted competency:  8
agil projektmanagement -- agile Projektmanagement
agil projektmanagement -- agil Projektmanagement
qualitätskontrolle beaufsichtigen -- Qualitätskontrolle
risikomanagement -- Risikomanagement
ressource verwalten -- Ressourcenmanagement
projekt managen -- Projektmanagement
projekt managen -- Projektmanagement
planen -- Planung
 ------


course:  14171
numbers of extracted competency:  8
agil projektmanagement -- agile Projektmanagement
agil projektmanagement -- agil Projektmanagement
qualitätskontrolle beaufsichtigen -- Qualitätskontrolle
risikomanagement -- Risikomanagement
ressource verwalten -- Ressourcenmanagement
projekt managen -- Projektmanagement
projekt managen -- Projektmanagement
planen -- Planung
 ------


course:  14172
numbers of extracted competency:  8
agil projektmanagement -- agile Projektmanagement
agil projektmanagement -- agil Projektmanagement
qualitätskontrolle beaufsichtigen -- Qualitätskontrolle
risikomanagement -- Risikomanag

numbers of extracted competency:  7
agil projektmanagement -- agile Projektmanagement
agil projektmanagement -- agile Projektmanagement
agil projektmanagement -- agil Projektmanagement
gutachten vorbereiten -- vorbereiten
vorbereitend unterrichten -- vorbereiten
abbauvorschlag vorbereiten -- vorbereiten
grab vorbereiten -- vorbereiten
 ------


course:  14206
numbers of extracted competency:  7
agil projektmanagement -- agile Projektmanagement
agil projektmanagement -- agile Projektmanagement
agil projektmanagement -- agil Projektmanagement
gutachten vorbereiten -- vorbereiten
vorbereitend unterrichten -- vorbereiten
abbauvorschlag vorbereiten -- vorbereiten
grab vorbereiten -- vorbereiten
 ------


course:  14207
numbers of extracted competency:  7
agil projektmanagement -- agile Projektmanagement
agil projektmanagement -- agile Projektmanagement
agil projektmanagement -- agil Projektmanagement
gutachten vorbereiten -- vorbereiten
vorbereitend unterrichten -- vorbereiten
abbauvorschla

numbers of extracted competency:  0
 ------


course:  14260
numbers of extracted competency:  0
 ------


course:  14261
numbers of extracted competency:  0
 ------


course:  14262
numbers of extracted competency:  0
 ------


course:  14263
numbers of extracted competency:  0
 ------


course:  14264
numbers of extracted competency:  0
 ------


course:  14265
numbers of extracted competency:  0
 ------


course:  14266
numbers of extracted competency:  0
 ------


course:  14267
numbers of extracted competency:  0
 ------


course:  14268
numbers of extracted competency:  0
 ------


course:  14269
numbers of extracted competency:  0
 ------


course:  14270
numbers of extracted competency:  0
 ------


course:  14271
numbers of extracted competency:  0
 ------


course:  14272
numbers of extracted competency:  0
 ------


course:  14273
numbers of extracted competency:  0
 ------


course:  14274
numbers of extracted competency:  0
 ------


course:  14275
numbers of extracted com

numbers of extracted competency:  3
geschäftsprozeß -- Geschäftsprozeß
planen -- Planung
planen -- Planung
 ------


course:  14362
numbers of extracted competency:  3
geschäftsprozeß -- Geschäftsprozeß
planen -- Planung
planen -- Planung
 ------


course:  14363
numbers of extracted competency:  3
geschäftsprozeß -- Geschäftsprozeß
planen -- Planung
planen -- Planung
 ------


course:  14364
numbers of extracted competency:  3
geschäftsprozeß -- Geschäftsprozeß
planen -- Planung
planen -- Planung
 ------


course:  14365
numbers of extracted competency:  3
geschäftsprozeß -- Geschäftsprozeß
planen -- Planung
planen -- Planung
 ------


course:  14366
numbers of extracted competency:  1
vorbereitend unterrichten -- Vorbereitung
 ------


course:  14367
numbers of extracted competency:  1
vorbereitend unterrichten -- Vorbereitung
 ------


course:  14368
numbers of extracted competency:  1
vorbereitend unterrichten -- Vorbereitung
 ------


course:  14369
numbers of extracted competency

In [32]:
Save_results(courses,benchmark=0.85)

course:  13800
numbers of extracted competency:  2
geschäftsprozeß -- Geschäftsprozeß
finanzbuchhaltung führen -- Finanzbuchhaltung
 ------


course:  13801
numbers of extracted competency:  2
personal einstellen -- Personalmaßnahme
projekt managen -- Projektverwaltung
 ------


course:  13802
numbers of extracted competency:  0
 ------


course:  13803
numbers of extracted competency:  1
statistik -- Statistik
 ------


course:  13804
numbers of extracted competency:  1
vertragsrecht -- Vertragsgenerierung
 ------


course:  13805
numbers of extracted competency:  6
messgerät überwachen -- Überwachung
persönlichkeitsentwicklung -- Personalentwicklung
überwachungseinrichtung überwachen -- Überwachung
personal entwickeln -- Personalentwicklung
erhebung überwachen -- Überwachung
überwachungsradar -- Überwachung
 ------


course:  13806
numbers of extracted competency:  6
eventmanagement durchführen -- Veranstaltungsmanagement
personal managen -- Personaladministration
personal verwalten 

numbers of extracted competency:  6
ertrag verwalten -- verwalten
verwaltungssystem managen -- Systemadministration
verwaltungssystem managen -- Systemadministration
verwaltungssystem managen -- Systemadministration
stall verwalten -- verwalten
software installieren -- Software-Installation
 ------


course:  13856
numbers of extracted competency:  9
ertrag verwalten -- verwalten
ertrag verwalten -- verwalten
verwaltungssystem managen -- Systemadministration
stall verwalten -- verwalten
stall verwalten -- verwalten
stellenbeschreibung verfassen -- beschreiben
stellenbeschreibung verfassen -- beschreiben
verwaltung erledigen -- Verwaltung
verwaltung erledigen -- Verwaltung
 ------


course:  13857
numbers of extracted competency:  3
wache stehen -- stehen
anderer führen -- anderer
anderer vertreten -- anderer
 ------


course:  13858
numbers of extracted competency:  5
sql server -- SQL Server
sql server -- SQL Server
sql server -- SQL Server
sql server -- SQL Server
backups durchführen

numbers of extracted competency:  32
stellenanalyse durchführen -- analysieren
stellenanalyse durchführen -- analysieren
stellenanalyse durchführen -- analysieren
stellenanalyse durchführen -- analysieren
stellenanalyse durchführen -- analysieren
stellenanalyse durchführen -- analysieren
stellenanalyse durchführen -- analysieren
darlehen analysieren -- analysieren
darlehen analysieren -- analysieren
darlehen analysieren -- analysieren
darlehen analysieren -- analysieren
darlehen analysieren -- analysieren
darlehen analysieren -- analysieren
darlehen analysieren -- analysieren
ofen installieren -- installieren
erhebungstechnik -- Technik
architekturdesign -- Architektur
architekturdesign -- Architektur
architekturdesign -- Architektur
artikulationstechnik -- Technik
problem lösen -- Problem
problem lösen -- Problem
problem lösen -- Problem
problem lösen -- Problem
problem lösen -- Problem
problem lösen -- Problem
problem lösen -- Problem
stellenbeschreibung verfassen -- beschreiben
flec

numbers of extracted competency:  31
stellenanalyse durchführen -- analysieren
stellenanalyse durchführen -- analysieren
stellenanalyse durchführen -- analysieren
stellenanalyse durchführen -- analysieren
stellenanalyse durchführen -- analysieren
stellenanalyse durchführen -- analysieren
stellenanalyse durchführen -- analysieren
stellenanalyse durchführen -- analysieren
stellenanalyse durchführen -- analysieren
stellenanalyse durchführen -- analysieren
stellenanalyse durchführen -- analysieren
darlehen analysieren -- analysieren
darlehen analysieren -- analysieren
darlehen analysieren -- analysieren
darlehen analysieren -- analysieren
darlehen analysieren -- analysieren
darlehen analysieren -- analysieren
darlehen analysieren -- analysieren
darlehen analysieren -- analysieren
darlehen analysieren -- analysieren
darlehen analysieren -- analysieren
darlehen analysieren -- analysieren
virtuell realität -- virtuell
stellenbeschreibung verfassen -- beschreiben
entscheidung treffen -- Entsch

numbers of extracted competency:  46
cloud-architektur konzipieren -- Cloud-Infrastruktur
modetrend -- Mode
messgerät überwachen -- überwachen
messgerät überwachen -- Überwachung
abfallentsorgung überwachen -- überwachen
dekontaminierungstechnik -- Bereitstellungstechnik
ofen installieren -- installieren
ofen installieren -- installieren
dokumentationsart -- dokumentieren
ertrag verwalten -- verwalten
ertrag verwalten -- verwalten
ertrag verwalten -- verwalten
ertrag verwalten -- verwalten
ertrag verwalten -- verwalten
ertrag verwalten -- verwalten
ertrag verwalten -- verwalten
ertrag verwalten -- verwalten
ertrag verwalten -- verwalten
firmware -- Firmware
erhebungstechnik -- Bereitstellungstechnik
hardware-materialie -- Hardware
hardware-materialie -- Hardware
überwachungseinrichtung überwachen -- überwachen
überwachungseinrichtung überwachen -- Überwachung
stall verwalten -- verwalten
stall verwalten -- verwalten
stall verwalten -- verwalten
stall verwalten -- verwalten
stall verwal

...

numbers of extracted competency:  3
wache stehen -- stehen
politik -- Politik
gesellschaft leisten -- Gesellschaft
 ------


course:  16555
numbers of extracted competency:  1
kommunikation -- Kommunikation
 ------


course:  16556
numbers of extracted competency:  0
 ------


course:  16557
numbers of extracted competency:  2
lesestrategie vermitteln -- lernstrategien
lernstrategien einsetzen -- lernstrategien
 ------


course:  16558
numbers of extracted competency:  2
stress standhalten -- stressen
stress vertragen -- stressen
 ------


course:  16559
numbers of extracted competency:  2
anderer führen -- anderer
anderer vertreten -- anderer
 ------


course:  16560
numbers of extracted competency:  6
wache stehen -- stehen
arbeitsmarktangebot -- Arbeitsmarkt
vorbereitend unterrichten -- Vorbereitung
persönlichkeitsentwicklung -- Persönlichkeitsentwicklung
arbeit leiten -- arbeiten
arbeitsmarkt -- Arbeitsmarkt
 ------


course:  16561
numbers of extracted competency:  13
kommunikatio

numbers of extracted competency:  3
energie -- Energie
fertigungsverfahren -- Fertigungsverfahren
kreativ denken -- Kreativität
 ------


course:  16621
numbers of extracted competency:  4
energie -- Energie
fertigungsverfahren -- Fertigungsverfahren
stellenbeschreibung verfassen -- Beschreibung
kreativ denken -- Kreativität
 ------


course:  16622
numbers of extracted competency:  5
energie -- Energie
fertigungsverfahren -- Fertigungsverfahren
fertigungsverfahren -- Fertigungsverfahren
gestaltungsprinzipien -- Gestaltungsprinzipien
kreativ denken -- Kreativität
 ------


course:  16623
numbers of extracted competency:  3
verantwortung übernehmen -- Eigenverantwortung
energie -- Energie
spiel betreiben -- spielen
 ------


course:  16624
numbers of extracted competency:  7
energie -- Energie
vorbereitend unterrichten -- Vorbereitung
verkokungsprozess -- prozessbezogen Vermittlung
verkokungsprozess -- prozessbezogen Aneignung
prozess der weingärung -- prozessbezogen Vermittlung
prozess

numbers of extracted competency:  39
persönlich fertigkeit entwickeln -- persönlich Entwicklung
orthopädisch physiotherapie -- Physiotherapeut
wache stehen -- stehen
wache stehen -- stehen
yoga -- Yoga
yoga -- Yoga
yoga -- Yogas
yoga -- Yoga
yoga -- Yogas
yoga -- Yoga
yoga -- Yogas
yoga -- Yogastunde
yoga -- Yogas
yoga -- Yogas
yoga -- Yogas
yoga -- Yoga
yoga -- Yoga
yoga -- Yogastunde
selbstreflexion üben -- Selbstreflexion
der persönlich entwicklung vorantreiben -- persönlich Entwicklung
der persönlich entwicklung vorantreiben -- persönlich Weiterentwicklung
deutsch -- deutsche
persönlichkeitsentwicklung -- persönlich Entwicklung
persönlichkeitsentwicklung -- persönlich Weiterentwicklung
physiotherapeut physiotherapeutinn assistieren -- Physiotherapeut
schwangerschaft -- Schwangere
personal entwickeln -- persönlich Entwicklung
geschichte unterrichten -- Geschichte
geschichte unterrichten -- Geschichte
philosophie -- Philosophie
philosophie -- Philosophie
verhaltenstherapie -- Behandl

numbers of extracted competency:  10
wache stehen -- stehen
wache stehen -- stehen
wache stehen -- stehen
staf -- Mitarbeiter
staf -- Mitarbeiter
staf -- Mitarbeiter
staf -- Mitarbeiter
vertraulichkeit beachten -- vertraulich
konflikt lösen -- Konflikt
entscheidung treffen -- entscheiden
 ------


course:  16718
numbers of extracted competency:  2
kundensegmentierung -- Kundensegment
problem lösen -- Problem
 ------


course:  16719
numbers of extracted competency:  1
spiel betreiben -- spielen
 ------


course:  16720
numbers of extracted competency:  12
gutachten vorbereiten -- vorbereiten
gutachten vorbereiten -- vorbereiten
vorbereitend unterrichten -- vorbereiten
vorbereitend unterrichten -- vorbereiten
vorbereitend unterrichten -- Vorbereitung
abbauvorschlag vorbereiten -- vorbereiten
abbauvorschlag vorbereiten -- vorbereiten
konflikt lösen -- Konflikt
konfliktmanagement -- Konfliktmanagement
grab vorbereiten -- vorbereiten
grab vorbereiten -- vorbereiten
checklist einhalten -- C

numbers of extracted competency:  1
wache stehen -- stehen
 ------


course:  16782
numbers of extracted competency:  1
wache stehen -- stehen
 ------


course:  16783
numbers of extracted competency:  5
softwarerahm -- Software
softwaredesign entwickeln -- Software-Entwicklung
unternehmertum -- unternehmerisch
entscheidung treffen -- entscheiden
planen -- planen
 ------


course:  16784
numbers of extracted competency:  13
datenbank führen -- Datenbankum
datenbank führen -- Datenbankum
datenbank führen -- Datenbankum
php -- PHP
datenbank -- Datenbankum
datenbank -- Datenbankum
datenbank -- Datenbankum
mysql -- MySQL
ertrag verwalten -- verwalten
stall verwalten -- verwalten
betrieblich ikt-system -- funktionierend System
planen -- planen
planen -- Planung
 ------


course:  16785
numbers of extracted competency:  1
linguistik -- sprachlich
 ------


course:  16786
numbers of extracted competency:  2
wache stehen -- stehen
gesellschaft leisten -- Gesellschaft
 ------


course:  16787
n

In [3]:
for i in range(10):
    if i >5:
         print(i)
   

6
7
8
9


In [5]:
%%time
Competence_extraction(courses,0,labels_embed,benchmark=0.85)

NameError: name 'Competence_extraction' is not defined

### 